In [2]:
import sqlite3
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import xml.etree.ElementTree as ET
import plotly.graph_objects as go
import re 

In [3]:
import pandas as pd
import sqlite3

# Connect to the database
db_path = 'database.sqlite'
conn = sqlite3.connect(db_path)

# Table names
table_names = ["Country", "League", "Match", "Player", "Player_Attributes", "Team", "Team_Attributes"]

# Query relevant tables
country_data = pd.read_sql_query("SELECT * FROM Country", conn)
league_data = pd.read_sql_query("SELECT * FROM League", conn)
match_data = pd.read_sql_query("SELECT * FROM Match", conn)
player_data = pd.read_sql_query("SELECT * FROM Player", conn)
player_attributes_data = pd.read_sql_query("SELECT * FROM Player_Attributes", conn)
team_data = pd.read_sql_query("SELECT * FROM Team", conn)
team_attributes_data = pd.read_sql_query("SELECT * FROM Team_Attributes", conn)

In [4]:
player_attributes_data.head()

id  player_fifa_api_id  player_api_id                 date  overall_rating  \
0   1              218353         505942  2016-02-18 00:00:00            67.0   
1   2              218353         505942  2015-11-19 00:00:00            67.0   
2   3              218353         505942  2015-09-21 00:00:00            62.0   
3   4              218353         505942  2015-03-20 00:00:00            61.0   
4   5              218353         505942  2007-02-22 00:00:00            61.0   

   potential preferred_foot attacking_work_rate defensive_work_rate  crossing  \
0       71.0          right              medium              medium      49.0   
1       71.0          right              medium              medium      49.0   
2       66.0          right              medium              medium      49.0   
3       65.0          right              medium              medium      48.0   
4       65.0          right              medium              medium      48.0   

   ...  vision  penalties  marking  standing_tackle  sliding_tackle  \
0  ...    54.0       48.0     65.0             69.0            69.0   
1  ...    54.0       48.0     65.0             69.0            69.0   
2  ...    54.0       48.0     65.0             66.0            69.0   
3  ...    53.0       47.0     62.0             63.0            66.0   
4  ...    53.0       47.0     62.0             63.0            66.0   

   gk_diving  gk_handling  gk_kicking  gk_positioning  gk_reflexes  
0        6.0         11.0        10.0             8.0          8.0  
1        6.0         11.0        10.0             8.0          8.0  
2        6.0         11.0        10.0             8.0          8.0  
3        5.0         10.0         9.0             7.0          7.0  
4        5.0         10.0         9.0             7.0          7.0  

[5 rows x 42 columns]

In [5]:
match = match_data.drop(columns=['B365H','B365D','B365A','BWH','BWD','BWA','IWH','IWD','IWA','LBH','LBD','LBA','PSH','PSD','PSA','WHH','WHD','WHA','SJH','SJD','SJA','VCH','VCD','VCA','GBH','GBD','GBA','BSH','BSD','BSA'])
match.head()

id  country_id  league_id     season  stage                 date  \
0   1           1          1  2008/2009      1  2008-08-17 00:00:00   
1   2           1          1  2008/2009      1  2008-08-16 00:00:00   
2   3           1          1  2008/2009      1  2008-08-16 00:00:00   
3   4           1          1  2008/2009      1  2008-08-17 00:00:00   
4   5           1          1  2008/2009      1  2008-08-16 00:00:00   

   match_api_id  home_team_api_id  away_team_api_id  home_team_goal  ...  \
0        492473              9987              9993               1  ...   
1        492474             10000              9994               0  ...   
2        492475              9984              8635               0  ...   
3        492476              9991              9998               5  ...   
4        492477              7947              9985               1  ...   

   away_player_10  away_player_11  goal  shoton  shotoff  foulcommit  card  \
0             NaN             NaN  None    None     None        None  None   
1             NaN             NaN  None    None     None        None  None   
2             NaN             NaN  None    None     None        None  None   
3             NaN             NaN  None    None     None        None  None   
4             NaN             NaN  None    None     None        None  None   

   cross  corner  possession  
0   None    None        None  
1   None    None        None  
2   None    None        None  
3   None    None        None  
4   None    None        None  

[5 rows x 85 columns]

In [6]:
player_attributes_data.columns

Index(['id', 'player_fifa_api_id', 'player_api_id', 'date', 'overall_rating',
       'potential', 'preferred_foot', 'attacking_work_rate',
       'defensive_work_rate', 'crossing', 'finishing', 'heading_accuracy',
       'short_passing', 'volleys', 'dribbling', 'curve', 'free_kick_accuracy',
       'long_passing', 'ball_control', 'acceleration', 'sprint_speed',
       'agility', 'reactions', 'balance', 'shot_power', 'jumping', 'stamina',
       'strength', 'long_shots', 'aggression', 'interceptions', 'positioning',
       'vision', 'penalties', 'marking', 'standing_tackle', 'sliding_tackle',
       'gk_diving', 'gk_handling', 'gk_kicking', 'gk_positioning',
       'gk_reflexes'],
      dtype='object')

In [7]:
player_data.columns

Index(['id', 'player_api_id', 'player_name', 'player_fifa_api_id', 'birthday',
       'height', 'weight'],
      dtype='object')

In [8]:
# Select the columns as a list and then merge
players = player_attributes_data[
    ['player_api_id', 'date', 'overall_rating', 'potential', 'preferred_foot', 
     'attacking_work_rate', 'defensive_work_rate', 'crossing', 'finishing', 
     'heading_accuracy', 'short_passing', 'volleys', 'dribbling', 'curve', 
     'free_kick_accuracy', 'long_passing', 'ball_control', 'acceleration', 
     'sprint_speed', 'agility', 'reactions', 'balance', 'shot_power', 'jumping', 
     'stamina', 'strength', 'long_shots', 'aggression', 'interceptions', 'positioning',
     'vision', 'penalties', 'marking', 'standing_tackle', 'sliding_tackle',
     'gk_diving', 'gk_handling', 'gk_kicking', 'gk_positioning', 'gk_reflexes']
].merge(player_data, how='left', on='player_api_id')
players.head()

player_api_id                 date  overall_rating  potential  \
0         505942  2016-02-18 00:00:00            67.0       71.0   
1         505942  2015-11-19 00:00:00            67.0       71.0   
2         505942  2015-09-21 00:00:00            62.0       66.0   
3         505942  2015-03-20 00:00:00            61.0       65.0   
4         505942  2007-02-22 00:00:00            61.0       65.0   

  preferred_foot attacking_work_rate defensive_work_rate  crossing  finishing  \
0          right              medium              medium      49.0       44.0   
1          right              medium              medium      49.0       44.0   
2          right              medium              medium      49.0       44.0   
3          right              medium              medium      48.0       43.0   
4          right              medium              medium      48.0       43.0   

   heading_accuracy  ...  gk_handling  gk_kicking  gk_positioning  \
0              71.0  ...         11.0        10.0             8.0   
1              71.0  ...         11.0        10.0             8.0   
2              71.0  ...         11.0        10.0             8.0   
3              70.0  ...         10.0         9.0             7.0   
4              70.0  ...         10.0         9.0             7.0   

   gk_reflexes  id         player_name  player_fifa_api_id  \
0          8.0   1  Aaron Appindangoye              218353   
1          8.0   1  Aaron Appindangoye              218353   
2          8.0   1  Aaron Appindangoye              218353   
3          7.0   1  Aaron Appindangoye              218353   
4          7.0   1  Aaron Appindangoye              218353   

              birthday  height  weight  
0  1992-02-29 00:00:00  182.88     187  
1  1992-02-29 00:00:00  182.88     187  
2  1992-02-29 00:00:00  182.88     187  
3  1992-02-29 00:00:00  182.88     187  
4  1992-02-29 00:00:00  182.88     187  

[5 rows x 46 columns]

In [9]:
Soccer = pd.read_sql(""" SELECT Match.id, Match.possession,Match.goal,Match.shoton,Match.shotoff,Match.foulcommit,Match.corner,Match.cross,
                Country.name AS country_name, League.name AS league_name, season, stage, date, HT.team_long_name AS  home_team, AT.team_long_name AS away_team, home_team_goal, away_team_goal 
                FROM Match
                JOIN Country on Country.id = Match.country_id
                JOIN League on League.id = Match.league_id
                LEFT JOIN Team AS HT on HT.team_api_id = Match.home_team_api_id
                LEFT JOIN Team AS AT on AT.team_api_id = Match.away_team_api_id
                ORDER by date;""", conn)
Soccer.head()

id possession  goal shoton shotoff foulcommit corner cross country_name  \
0  24559       None  None   None    None       None   None  None  Switzerland   
1  24560       None  None   None    None       None   None  None  Switzerland   
2  24561       None  None   None    None       None   None  None  Switzerland   
3  24562       None  None   None    None       None   None  None  Switzerland   
4  24613       None  None   None    None       None   None  None  Switzerland   

                league_name     season  stage                 date  \
0  Switzerland Super League  2008/2009      1  2008-07-18 00:00:00   
1  Switzerland Super League  2008/2009      1  2008-07-19 00:00:00   
2  Switzerland Super League  2008/2009      1  2008-07-20 00:00:00   
3  Switzerland Super League  2008/2009      1  2008-07-20 00:00:00   
4  Switzerland Super League  2008/2009      2  2008-07-23 00:00:00   

         home_team                away_team  home_team_goal  away_team_goal  
0   BSC Young Boys                 FC Basel               1               2  
1         FC Aarau                  FC Sion               3               1  
2        FC Luzern                 FC Vaduz               1               2  
3  Neuchâtel Xamax                FC Zürich               1               2  
4         FC Basel  Grasshopper Club Zürich               1               0

In [10]:
# Players Statistics
def aggregate_player_stats(match_data):
    player_stats = {}

    # Process each match
    for _, row in match_data.iterrows():
        # Parse scorers (goals) and assisters (assists)
        Scorers = re.findall(r'<player1>(.*?)</player1>', str(row['goal']))
        Assisters = re.findall(r'<player2>(.*?)</player2>', str(row['goal']))

        # Update goals
        for player in Scorers:
            player_stats[player] = player_stats.get(player, {'goals': 0, 'assists': 0, 'shots': 0})
            player_stats[player]['goals'] += 1

        # Update assists
        for player in Assisters:
            player_stats[player] = player_stats.get(player, {'goals': 0, 'assists': 0, 'shots': 0})
            player_stats[player]['assists'] += 1

        # Parse shots (if structured similarly to goals/assists)
        # Assume `shoton` contains <player1>...</player1> tags
        shot_players = re.findall(r'<player1>(.*?)</player1>', str(row['shoton']))
        for player in shot_players:
            player_stats[player] = player_stats.get(player, {'goals': 0, 'assists': 0, 'shots': 0})
            player_stats[player]['shots'] += 1

    # Dataframe Conversion
    stats_df = pd.DataFrame.from_dict(player_stats, orient='index')
    stats_df.index.name = 'player_api_id'
    stats_df.reset_index(inplace=True)
    return stats_df

In [11]:
Stats_player = aggregate_player_stats(Soccer)
Stats_player.reset_index(inplace=True)
players.head()

player_api_id                 date  overall_rating  potential  \
0         505942  2016-02-18 00:00:00            67.0       71.0   
1         505942  2015-11-19 00:00:00            67.0       71.0   
2         505942  2015-09-21 00:00:00            62.0       66.0   
3         505942  2015-03-20 00:00:00            61.0       65.0   
4         505942  2007-02-22 00:00:00            61.0       65.0   

  preferred_foot attacking_work_rate defensive_work_rate  crossing  finishing  \
0          right              medium              medium      49.0       44.0   
1          right              medium              medium      49.0       44.0   
2          right              medium              medium      49.0       44.0   
3          right              medium              medium      48.0       43.0   
4          right              medium              medium      48.0       43.0   

   heading_accuracy  ...  gk_handling  gk_kicking  gk_positioning  \
0              71.0  ...         11.0        10.0             8.0   
1              71.0  ...         11.0        10.0             8.0   
2              71.0  ...         11.0        10.0             8.0   
3              70.0  ...         10.0         9.0             7.0   
4              70.0  ...         10.0         9.0             7.0   

   gk_reflexes  id         player_name  player_fifa_api_id  \
0          8.0   1  Aaron Appindangoye              218353   
1          8.0   1  Aaron Appindangoye              218353   
2          8.0   1  Aaron Appindangoye              218353   
3          7.0   1  Aaron Appindangoye              218353   
4          7.0   1  Aaron Appindangoye              218353   

              birthday  height  weight  
0  1992-02-29 00:00:00  182.88     187  
1  1992-02-29 00:00:00  182.88     187  
2  1992-02-29 00:00:00  182.88     187  
3  1992-02-29 00:00:00  182.88     187  
4  1992-02-29 00:00:00  182.88     187  

[5 rows x 46 columns]

In [12]:
Stats_player['player_api_id'] = pd.to_numeric(Stats_player['player_api_id'])
player_profile = pd.merge(players, Stats_player, how='left', on='player_api_id')
player_profile.fillna(0, inplace=True)

In [13]:
# Calculate total contributions (goals + assists)
player_profile['total_contributions'] = player_profile['goals'] + player_profile['assists']

In [14]:
# Initialize an empty list to store player-season goal data
player_season_goals = []

# Iterate through the matches to extract goals and associated seasons
for _, row in match.iterrows():
    Scorers = re.findall(r'<player1>(.*?)</player1>', str(row['goal']))
    season = row['season']

    for player_id in Scorers:
        player_season_goals.append({'player_api_id': int(player_id), 'season': season, 'goals': 1})

# Convert the data into a DataFrame
player_season_goals_df = pd.DataFrame(player_season_goals)

# Aggregate goals by player and season
player_goals_by_season = player_season_goals_df.groupby(['player_api_id', 'season']).sum().reset_index()

# Verify the output
player_goals_by_season.head()

player_api_id     season  goals
0           2752  2011/2012      1
1           2752  2012/2013      1
2           2752  2013/2014      1
3           2752  2014/2015      5
4           2768  2011/2012      3

In [15]:
# Get players stats per season
merged_df = player_profile[['player_api_id', 'player_name', 'player_fifa_api_id', 'birthday', 'height', 'weight', 'index', 'assists', 'shots', 'total_contributions']].merge(
    player_goals_by_season,
    how='left',  # Use 'left' join to retain all rows from player_profile
    on='player_api_id'
)

# clean and verify merged dataframe
merged_df['goals'] = merged_df['goals'].fillna(0)
merged_df['season'] = merged_df['season'].fillna('unknown')
merged_df = merged_df.drop_duplicates(subset=['player_api_id', 'season'])

merged_df.head(10)

player_api_id         player_name  player_fifa_api_id  \
0           505942  Aaron Appindangoye              218353   
5           155782     Aaron Cresswell              189615   
6           155782     Aaron Cresswell              189615   
71          162549         Aaron Doran              186170   
97           30572       Aaron Galindo              140161   
120          23780        Aaron Hughes               17725   
121          23780        Aaron Hughes               17725   
170          27316          Aaron Hunt              158138   
171          27316          Aaron Hunt              158138   
172          27316          Aaron Hunt              158138   

                birthday  height  weight   index  assists  shots  \
0    1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
5    1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
6    1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
71   1991-05-13 00:00:00  170.18     163     0.0      0.0    0.0   
97   1982-05-08 00:00:00  182.88     198     0.0      0.0    0.0   
120  1979-11-08 00:00:00  182.88     154   849.0      0.0   12.0   
121  1979-11-08 00:00:00  182.88     154   849.0      0.0   12.0   
170  1986-09-04 00:00:00  182.88     161   672.0     11.0   47.0   
171  1986-09-04 00:00:00  182.88     161   672.0     11.0   47.0   
172  1986-09-04 00:00:00  182.88     161   672.0     11.0   47.0   

     total_contributions     season  goals  
0                    0.0    unknown    0.0  
5                   12.0  2014/2015    2.0  
6                   12.0  2015/2016    2.0  
71                   0.0    unknown    0.0  
97                   0.0    unknown    0.0  
120                  2.0  2010/2011    1.0  
121                  2.0  2013/2014    1.0  
170                 51.0  2008/2009    2.0  
171                 51.0  2009/2010    9.0  
172                 51.0  2010/2011    3.0

In [16]:
player_attributes_data.columns

Index(['id', 'player_fifa_api_id', 'player_api_id', 'date', 'overall_rating',
       'potential', 'preferred_foot', 'attacking_work_rate',
       'defensive_work_rate', 'crossing', 'finishing', 'heading_accuracy',
       'short_passing', 'volleys', 'dribbling', 'curve', 'free_kick_accuracy',
       'long_passing', 'ball_control', 'acceleration', 'sprint_speed',
       'agility', 'reactions', 'balance', 'shot_power', 'jumping', 'stamina',
       'strength', 'long_shots', 'aggression', 'interceptions', 'positioning',
       'vision', 'penalties', 'marking', 'standing_tackle', 'sliding_tackle',
       'gk_diving', 'gk_handling', 'gk_kicking', 'gk_positioning',
       'gk_reflexes'],
      dtype='object')

In [17]:
players_full = merged_df.merge(player_attributes_data[['player_api_id', 'date', 'overall_rating',
       'potential', 'preferred_foot', 'penalties']], how='left', on='player_api_id')
players_full.head(20)

player_api_id         player_name  player_fifa_api_id  \
0          505942  Aaron Appindangoye              218353   
1          505942  Aaron Appindangoye              218353   
2          505942  Aaron Appindangoye              218353   
3          505942  Aaron Appindangoye              218353   
4          505942  Aaron Appindangoye              218353   
5          155782     Aaron Cresswell              189615   
6          155782     Aaron Cresswell              189615   
7          155782     Aaron Cresswell              189615   
8          155782     Aaron Cresswell              189615   
9          155782     Aaron Cresswell              189615   
10         155782     Aaron Cresswell              189615   
11         155782     Aaron Cresswell              189615   
12         155782     Aaron Cresswell              189615   
13         155782     Aaron Cresswell              189615   
14         155782     Aaron Cresswell              189615   
15         155782     Aaron Cresswell              189615   
16         155782     Aaron Cresswell              189615   
17         155782     Aaron Cresswell              189615   
18         155782     Aaron Cresswell              189615   
19         155782     Aaron Cresswell              189615   

               birthday  height  weight   index  assists  shots  \
0   1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
1   1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
2   1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
3   1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
4   1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
5   1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
6   1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
7   1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
8   1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
9   1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
10  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
11  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
12  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
13  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
14  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
15  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
16  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
17  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
18  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
19  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   

    total_contributions     season  goals                 date  \
0                   0.0    unknown    0.0  2016-02-18 00:00:00   
1                   0.0    unknown    0.0  2015-11-19 00:00:00   
2                   0.0    unknown    0.0  2015-09-21 00:00:00   
3                   0.0    unknown    0.0  2015-03-20 00:00:00   
4                   0.0    unknown    0.0  2007-02-22 00:00:00   
5                  12.0  2014/2015    2.0  2016-04-21 00:00:00   
6                  12.0  2014/2015    2.0  2016-04-07 00:00:00   
7                  12.0  2014/2015    2.0  2016-01-07 00:00:00   
8                  12.0  2014/2015    2.0  2015-12-24 00:00:00   
9                  12.0  2014/2015    2.0  2015-12-17 00:00:00   
10                 12.0  2014/2015    2.0  2015-10-16 00:00:00   
11                 12.0  2014/2015    2.0  2015-09-25 00:00:00   
12                 12.0  2014/2015    2.0  2015-09-21 00:00:00   
13                 12.0  2014/2015    2.0  2015-01-09 00:00:00   
14                 12.0  2014/2015    2.0  2014-12-05 00:00:00   
15                 12.0  2014/2015    2.0  2014-11-07 00:00:00   
16                 12.0  2014/2015    2.0  2014-09-18 00:00:00   
17                 12.0  2014/2015    2.0  2014-05-02 00:00:00   
18                 12.0  2014/2015    2.0  2014-04-04 00:00:

In [18]:
# Check all unique seasons in the dataset
print(players_full["season"].unique())


['unknown' '2014/2015' '2015/2016' '2010/2011' '2013/2014' '2008/2009'
 '2009/2010' '2011/2012' '2012/2013']


In [19]:
import pandas as pd

# Assuming df is your original dataframe

# Drop duplicate rows based on player_name and season
clean_p = players_full.drop_duplicates(subset=["player_name", "season"])

# To check if duplicates were removed
clean_p.head()

player_api_id         player_name  player_fifa_api_id  \
0          505942  Aaron Appindangoye              218353   
5          155782     Aaron Cresswell              189615   
38         155782     Aaron Cresswell              189615   
71         162549         Aaron Doran              186170   
97          30572       Aaron Galindo              140161   

               birthday  height  weight   index  assists  shots  \
0   1992-02-29 00:00:00  182.88     187     0.0      0.0    0.0   
5   1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
38  1989-12-15 00:00:00  170.18     146  4115.0      8.0   22.0   
71  1991-05-13 00:00:00  170.18     163     0.0      0.0    0.0   
97  1982-05-08 00:00:00  182.88     198     0.0      0.0    0.0   

    total_contributions     season  goals                 date  \
0                   0.0    unknown    0.0  2016-02-18 00:00:00   
5                  12.0  2014/2015    2.0  2016-04-21 00:00:00   
38                 12.0  2015/2016    2.0  2016-04-21 00:00:00   
71                  0.0    unknown    0.0  2016-01-07 00:00:00   
97                  0.0    unknown    0.0  2016-04-21 00:00:00   

    overall_rating  potential preferred_foot  penalties  
0             67.0       71.0          right       48.0  
5             74.0       76.0           left       59.0  
38            74.0       76.0           left       59.0  
71            65.0       67.0          right       61.0  
97            69.0       69.0          right       37.0

In [20]:
# Step 2: Define the Performance Metric
clean_p['performance_metric'] = (
    0.5 * clean_p['overall_rating'] +
    0.3 * clean_p['potential'] +
    0.2 * clean_p.get('other_attribute', 0)  # Add additional attributes as needed
)

# Step 3: Identify Best Performers of Each Season
top_performers = (
    clean_p.groupby('season')
    .apply(lambda x: x.nlargest(10, 'performance_metric'))  # Top 5 performers
    .reset_index(drop=True)
)

# Step 4 Update: Filter players with data across multiple seasons
player_season_counts = clean_p.groupby('player_name')['season'].nunique()
players_with_multiple_seasons = player_season_counts[player_season_counts > 1].index

# Step 5: Visualization with Plotly
import plotly.express as px

# Top Performers Per Season
fig1 = px.bar(
    top_performers,
    x='season',
    y='performance_metric',
    color='player_name',
    title="Top Performers of Each Season",
    labels={'performance_metric': 'Performance Metric'},
    hover_data=['player_name', 'overall_rating', 'potential']
)
fig1.show()

/tmp/ipykernel_316084/1471523254.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  clean_p['performance_metric'] = (


In [21]:
clean_p.info()

<class 'pandas.core.frame.DataFrame'>
Index: 17277 entries, 0 to 352584
Data columns (total 18 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   player_api_id        17277 non-null  int64  
 1   player_name          17277 non-null  object 
 2   player_fifa_api_id   17277 non-null  int64  
 3   birthday             17277 non-null  object 
 4   height               17277 non-null  float64
 5   weight               17277 non-null  int64  
 6   index                17277 non-null  float64
 7   assists              17277 non-null  float64
 8   shots                17277 non-null  float64
 9   total_contributions  17277 non-null  float64
 10  season               17277 non-null  object 
 11  goals                17277 non-null  float64
 12  date                 17277 non-null  object 
 13  overall_rating       17277 non-null  float64
 14  potential            17277 non-null  float64
 15  preferred_foot       17277 non-null  obj

In [22]:
clean_p['date'] = pd.to_datetime(clean_p['date'], format='%Y-%m-%d %H:%M:%S')
clean_p['birthday'] = pd.to_datetime(clean_p['birthday'], format='%Y-%m-%d %H:%M:%S')
clean_p.info()

<class 'pandas.core.frame.DataFrame'>
Index: 17277 entries, 0 to 352584
Data columns (total 18 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   player_api_id        17277 non-null  int64         
 1   player_name          17277 non-null  object        
 2   player_fifa_api_id   17277 non-null  int64         
 3   birthday             17277 non-null  datetime64[ns]
 4   height               17277 non-null  float64       
 5   weight               17277 non-null  int64         
 6   index                17277 non-null  float64       
 7   assists              17277 non-null  float64       
 8   shots                17277 non-null  float64       
 9   total_contributions  17277 non-null  float64       
 10  season               17277 non-null  object        
 11  goals                17277 non-null  float64       
 12  date                 17277 non-null  datetime64[ns]
 13  overall_rating       17277 non-null

/tmp/ipykernel_316084/3088083583.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_316084/3088083583.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Dropping the ``date`` Column in Our Project
#### **In our dataset, the date column records the exact date of each entry. However, for our analysis, we are primarily interested in unique player-season combinations and the performance metrics (such as goals, assists, etc.) for each player over a season. The exact date does not add any significant value to our analysis, as we're focused on the season-level data.**

In [23]:
# Drop the 'date' column if it's no longer needed
clean_p = clean_p.drop(columns=["date"])

# Check the updated dataframe
print(clean_p.head())

    player_api_id         player_name  player_fifa_api_id   birthday  height  \
0          505942  Aaron Appindangoye              218353 1992-02-29  182.88   
5          155782     Aaron Cresswell              189615 1989-12-15  170.18   
38         155782     Aaron Cresswell              189615 1989-12-15  170.18   
71         162549         Aaron Doran              186170 1991-05-13  170.18   
97          30572       Aaron Galindo              140161 1982-05-08  182.88   

    weight   index  assists  shots  total_contributions     season  goals  \
0      187     0.0      0.0    0.0                  0.0    unknown    0.0   
5      146  4115.0      8.0   22.0                 12.0  2014/2015    2.0   
38     146  4115.0      8.0   22.0                 12.0  2015/2016    2.0   
71     163     0.0      0.0    0.0                  0.0    unknown    0.0   
97     198     0.0      0.0    0.0                  0.0    unknown    0.0   

    overall_rating  potential preferred_foot  penalties 

In [24]:
clean_p.head()

player_api_id         player_name  player_fifa_api_id   birthday  height  \
0          505942  Aaron Appindangoye              218353 1992-02-29  182.88   
5          155782     Aaron Cresswell              189615 1989-12-15  170.18   
38         155782     Aaron Cresswell              189615 1989-12-15  170.18   
71         162549         Aaron Doran              186170 1991-05-13  170.18   
97          30572       Aaron Galindo              140161 1982-05-08  182.88   

    weight   index  assists  shots  total_contributions     season  goals  \
0      187     0.0      0.0    0.0                  0.0    unknown    0.0   
5      146  4115.0      8.0   22.0                 12.0  2014/2015    2.0   
38     146  4115.0      8.0   22.0                 12.0  2015/2016    2.0   
71     163     0.0      0.0    0.0                  0.0    unknown    0.0   
97     198     0.0      0.0    0.0                  0.0    unknown    0.0   

    overall_rating  potential preferred_foot  penalties  performance_metric  
0             67.0       71.0          right       48.0                54.8  
5             74.0       76.0           left       59.0                59.8  
38            74.0       76.0           left       59.0                59.8  
71            65.0       67.0          right       61.0                52.6  
97            69.0       69.0          right       37.0                55.2

In [25]:
import plotly.graph_objects as go

# Filter data for a specific season (e.g., 2015/2016)
season_data = clean_p[clean_p['season'] == '2015/2016']

# Sort players by goals and pick the top 10
top_players = season_data.sort_values(by='goals', ascending=False).head(10)

# Create a bar chart for goals scored by the top 10 players
fig = go.Figure(go.Bar(
    x=top_players['player_name'],
    y=top_players['goals'],
    orientation='v',
    marker=dict(color='springgreen')
))

# Update layout with dark theme
fig.update_layout(
    title='Top 10 Goal Scorers in 2015/2016',
    xaxis_title='Player Name',
    yaxis_title='Goals Scored',
    xaxis_tickangle=45,  # Rotate x-axis labels for better readability
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
    font=dict(color='white'),  # Change font color to white
    title_font=dict(color='white'),  # Change title font color
    xaxis=dict(tickfont=dict(color='white')),  # Change x-axis tick color
    yaxis=dict(tickfont=dict(color='white'))  # Change y-axis tick color
)

# Show plot
fig.show()


In [26]:
import plotly.graph_objects as go

# Filter data for a specific season (e.g., 2015/2016)
season_data = clean_p[clean_p['season'] == '2015/2016']

# Sort players by assists and pick the top 10
top_assists = season_data.sort_values(by='assists', ascending=False).head(10)

# Create a bar chart for top 10 players by assists
fig = go.Figure(go.Bar(
    x=top_assists['player_name'],
    y=top_assists['assists'],
    orientation='v',
    marker=dict(color='#9203ff')
))

# Update layout with dark theme
fig.update_layout(
    title='Top 10 Assists Leaders in 2015/2016',
    xaxis_title='Player Name',
    yaxis_title='Assists',
    xaxis_tickangle=45,  # Rotate x-axis labels for better readability
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
    font=dict(color='white'),  # Change font color to white
    title_font=dict(color='white'),  # Change title font color
    xaxis=dict(tickfont=dict(color='white')),  # Change x-axis tick color
    yaxis=dict(tickfont=dict(color='white'))  # Change y-axis tick color
)

# Show plot
fig.show()


In [27]:
# Filter data for a specific season (e.g., 2015/2016)
season_data = clean_p[clean_p['season'] == '2015/2016']

# Create a scatter plot for goals vs total contributions
fig = go.Figure(go.Scatter(
    x=season_data['goals'],
    y=season_data['total_contributions'],
    mode='markers',
    marker=dict(color='cyan', size=10)
))

# Update layout with dark theme
fig.update_layout(
    title='Goals vs Total Contributions in 2015/2016',
    xaxis_title='Goals',
    yaxis_title='Total Contributions',
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
    font=dict(color='white'),  # Change font color to white
    title_font=dict(color='white'),  # Change title font color
    xaxis=dict(tickfont=dict(color='white')),  # Change x-axis tick color
    yaxis=dict(tickfont=dict(color='white'))  # Change y-axis tick color
)

# Show plot
fig.show()


In [28]:
# Filter data for a specific season (e.g., 2015/2016)
season_data = clean_p[clean_p['season'] == '2015/2016']

# Create a scatter plot for overall rating vs performance metric
fig = go.Figure(go.Scatter(
    x=season_data['overall_rating'],
    y=season_data['performance_metric'],
    mode='markers',
    marker=dict(color='magenta', size=10)
))

# Update layout with dark theme
fig.update_layout(
    title='Overall Rating vs Performance Metric in 2015/2016',
    xaxis_title='Overall Rating',
    yaxis_title='Performance Metric',
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
    font=dict(color='white'),  # Change font color to white
    title_font=dict(color='white'),  # Change title font color
    xaxis=dict(tickfont=dict(color='white')),  # Change x-axis tick color
    yaxis=dict(tickfont=dict(color='white'))  # Change y-axis tick color
)

# Show plot
fig.show()


In [29]:
import plotly.graph_objects as go
import pandas as pd

# Select only numeric columns for correlation analysis
numeric_columns = clean_p[['goals', 'assists', 'shots', 'total_contributions', 'performance_metric', 'overall_rating', 'potential', 'penalties']]

# Calculate the correlation matrix
correlation_matrix = numeric_columns.corr()

# Create the heatmap using Plotly
fig = go.Figure(data=go.Heatmap(
    z=correlation_matrix.values,
    x=correlation_matrix.columns,
    y=correlation_matrix.columns,
    colorscale='Viridis',  # Color scale for the heatmap
    colorbar=dict(title='Correlation', tickvals=[-1, 0, 1], ticktext=['-1', '0', '1']),  # Customize the color bar
    showscale=True
))

# Update layout for dark background
fig.update_layout(
    title='Correlation Heatmap of Numerical Features',
    xaxis_title='Features',
    yaxis_title='Features',
    title_font=dict(color='white'),
    font=dict(color='white'),
    xaxis=dict(tickfont=dict(color='white')),
    yaxis=dict(tickfont=dict(color='white')),
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
)

# Show the plot
fig.show()

In [30]:
import plotly.graph_objects as go

# Filter the DataFrame for the 2015/2016 season
season_2015_2016 = clean_p[clean_p['season'] == '2015/2016']

# Sort the filtered DataFrame by 'overall_rating' and get the top 10 players
top_10_players_2015_2016 = season_2015_2016[['player_name', 'overall_rating']].sort_values(by='overall_rating', ascending=False).head(10)

# Create the bar chart using Plotly
fig = go.Figure(data=go.Bar(
    x=top_10_players_2015_2016['player_name'],
    y=top_10_players_2015_2016['overall_rating'],
    marker=dict(color='#ff3503'),  # Color for the bars
))

# Update layout for the dark background
fig.update_layout(
    title='Top 10 Players by Overall Rating (2015/2016)',
    xaxis_title='Player Name',
    yaxis_title='Overall Rating',
    title_font=dict(color='white'),
    font=dict(color='white'),
    xaxis=dict(tickfont=dict(color='white')),
    yaxis=dict(tickfont=dict(color='white')),
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
    barmode='group',
)

# Show the plot
fig.show()


In [31]:
import plotly.graph_objects as go

# Filter the DataFrame for the 2015/2016 season
season_2015_2016 = clean_p[clean_p['season'] == '2015/2016']

# Sort the filtered DataFrame by 'potential' and get the top 10 players
top_10_players_potential_2015_2016 = season_2015_2016[['player_name', 'potential']].sort_values(by='potential', ascending=False).head(10)

# Create the bar chart using Plotly
fig = go.Figure(data=go.Bar(
    x=top_10_players_potential_2015_2016['player_name'],
    y=top_10_players_potential_2015_2016['potential'],
    marker=dict(color='#ff29cd'),  # Color for the bars
))

# Update layout for the dark background
fig.update_layout(
    title='Top 10 Players by Potential (2015/2016)',
    xaxis_title='Player Name',
    yaxis_title='Potential',
    title_font=dict(color='white'),
    font=dict(color='white'),
    xaxis=dict(tickfont=dict(color='white')),
    yaxis=dict(tickfont=dict(color='white')),
    plot_bgcolor='rgb(20, 20, 20)',  # Dark background for the plot
    paper_bgcolor='rgb(30, 30, 30)',  # Dark background for the entire figure
    barmode='group',
)

# Show the plot
fig.show()


In [32]:
import pandas as pd
import sqlite3
import xml.etree.ElementTree as ET

# Define functions to parse the XML data
def parse_possession(xml_data):
    try:
        root = ET.fromstring(xml_data)
        home_pos = root.find(".//homepos")
        away_pos = root.find(".//awaypos")
        return {
            "homepos": int(home_pos.text) if home_pos is not None else 0,
            "awaypos": int(away_pos.text) if away_pos is not None else 0
        }
    except Exception:
        return {"homepos": 0, "awaypos": 0}

def extract_fouls_committed(xml_data):
    try:
        root = ET.fromstring(xml_data)
        fouls = root.find(".//foulscommitted")
        return int(fouls.text) if fouls is not None else 0
    except Exception:
        return 0

def extract_card_counts(xml_data):
    try:
        root = ET.fromstring(xml_data)
        yellow_cards = root.find(".//ycard")
        red_cards = root.find(".//rcard")
        return {
            "yellow_cards": int(yellow_cards.text) if yellow_cards is not None else 0,
            "red_cards": int(red_cards.text) if red_cards is not None else 0
        }
    except Exception:
        return {"yellow_cards": 0, "red_cards": 0}

def extract_crosses_and_corners(xml_data):
    try:
        root = ET.fromstring(xml_data)
        crosses = root.find(".//crosses")
        corners = root.find(".//corners")
        return {
            "crosses": int(crosses.text) if crosses is not None else 0,
            "corners": int(corners.text) if corners is not None else 0
        }
    except Exception:
        return {"crosses": 0, "corners": 0}

# Connect to the database
conn = sqlite3.connect("database.sqlite")

# Fetch possession data
possession_query = "SELECT match_api_id, possession FROM Match WHERE possession IS NOT NULL;"
possession_data = pd.read_sql_query(possession_query, conn)
possession_values = possession_data['possession'].apply(parse_possession)
possession_data['homepos'] = possession_values.apply(lambda x: x['homepos'])
possession_data['awaypos'] = possession_values.apply(lambda x: x['awaypos'])
possession_cleaned = possession_data[['match_api_id', 'homepos', 'awaypos']]

# Fetch foul commit, card, and cross data
columns_query = """
SELECT 
    match_api_id,
    foulcommit,
    card,
    cross
FROM Match
WHERE foulcommit IS NOT NULL OR card IS NOT NULL OR cross IS NOT NULL;
"""
columns_data = pd.read_sql_query(columns_query, conn)
columns_data['fouls_committed'] = columns_data['foulcommit'].apply(extract_fouls_committed)
card_counts = columns_data['card'].apply(extract_card_counts)
columns_data['yellow_cards'] = card_counts.apply(lambda x: x['yellow_cards'])
columns_data['red_cards'] = card_counts.apply(lambda x: x['red_cards'])
cross_counts = columns_data['cross'].apply(extract_crosses_and_corners)
columns_data['crosses'] = cross_counts.apply(lambda x: x['crosses'])
columns_data['corners'] = cross_counts.apply(lambda x: x['corners'])
columns_cleaned = columns_data[['match_api_id', 'fouls_committed', 'yellow_cards', 'red_cards', 'crosses', 'corners']]

# Fetch match details
match_details_query = """
SELECT 
    match_api_id,
    TeamHome.team_long_name AS home_team,
    TeamAway.team_long_name AS away_team,
    home_team_goal,
    away_team_goal
FROM Match
LEFT JOIN Team AS TeamHome ON Match.home_team_api_id = TeamHome.team_api_id
LEFT JOIN Team AS TeamAway ON Match.away_team_api_id = TeamAway.team_api_id;
"""
match_details = pd.read_sql_query(match_details_query, conn)

# Combine all datasets
final_combined_data = pd.merge(columns_cleaned, possession_cleaned, on='match_api_id', how='inner')
final_dataset = pd.merge(final_combined_data, match_details, on='match_api_id', how='inner')

# Reorder columns
ordered_columns = [
    'match_api_id', 'home_team', 'away_team', 'home_team_goal', 'away_team_goal',
    'homepos', 'awaypos', 'crosses', 'corners', 'yellow_cards',
    'red_cards', 'fouls_committed'
]
final_dataset_ordered = final_dataset[ordered_columns]

# Display the final DataFrame
final_dataset_ordered.head(30)

match_api_id             home_team             away_team  home_team_goal  \
0         489042     Manchester United      Newcastle United               1   
1         489043               Arsenal  West Bromwich Albion               1   
2         489044            Sunderland             Liverpool               0   
3         489045       West Ham United        Wigan Athletic               2   
4         489046           Aston Villa       Manchester City               4   
5         489047               Everton      Blackburn Rovers               2   
6         489048         Middlesbrough     Tottenham Hotspur               2   
7         489049      Bolton Wanderers            Stoke City               3   
8         489050             Hull City                Fulham               2   
9         489051               Chelsea            Portsmouth               4   
10        489132     Manchester United       West Ham United               2   
11        489133               Arsenal     Tottenham Hotspur               4   
12        489134         Middlesbrough       Manchester City               2   
13        489135      Bolton Wanderers               Everton               0   
14        489136             Hull City               Chelsea               0   
15        489137            Stoke City            Sunderland               1   
16        489138             Liverpool            Portsmouth               1   
17        489139           Aston Villa      Blackburn Rovers               3   
18        489140      Newcastle United  West Bromwich Albion               2   
19        489141                Fulham        Wigan Athletic               2   
20        489142     Manchester United             Hull City               4   
21        489143     Tottenham Hotspur             Liverpool               2   
22        489144               Everton                Fulham               1   
23        489145         Middlesbrough       West Ham United               1   
24        489146      Newcastle United           Aston Villa               2   
25        489147      Bolton Wanderers       Manchester City               2   
26        489148  West Bromwich Albion      Blackburn Rovers               2   
27        489149            Portsmouth        Wigan Athletic               1   
28        489150            Stoke City               Arsenal               2   
29        489151               Chelsea            Sunderland               5   

    away_team_goal  homepos  awaypos  crosses  corners  yellow_cards  \
0                1       56       44        1        1             0   
1                0       65       35        1        1             0   
2                1       45       55        1        1             0   
3                1       50       50        1        1             0   
4                2       51       49        1        1             0   
5                3       46       54        1        1             0   
6                1       49       51        1        1             0   
7                1       58       42        1        1             0   
8                1       49       51        1        1             0   
9                0       57       43        1        1             0   
10               0       59       41        1        1             0   
11               4       63       37        1        1             0   
12               0       48       52        1        1             0   
13               1       55       45        1        1             0   
14               3        0        0        1        1             0   
15               0       49       51        1        1             0   
16               0       57       43        1        1             0   
17               2       51       49        1        1             0   
18               1       45       55        1        1             0   
19               0       55       45        1        1             0   
20         

In [33]:
country_leagues = final_dataset_ordered.merge(match[['match_api_id', 'season', 'country_id', 'league_id']], how='left', on='match_api_id')

In [34]:
country_leagues.head()

match_api_id          home_team             away_team  home_team_goal  \
0        489042  Manchester United      Newcastle United               1   
1        489043            Arsenal  West Bromwich Albion               1   
2        489044         Sunderland             Liverpool               0   
3        489045    West Ham United        Wigan Athletic               2   
4        489046        Aston Villa       Manchester City               4   

   away_team_goal  homepos  awaypos  crosses  corners  yellow_cards  \
0               1       56       44        1        1             0   
1               0       65       35        1        1             0   
2               1       45       55        1        1             0   
3               1       50       50        1        1             0   
4               2       51       49        1        1             0   

   red_cards  fouls_committed     season  country_id  league_id  
0          0                1  2008/2009        1729       1729  
1          0                1  2008/2009        1729       1729  
2          0                1  2008/2009        1729       1729  
3          0                1  2008/2009        1729       1729  
4          0                1  2008/2009        1729       1729

In [35]:
# Fetch league names using 'id' as the key
league_names_query = """
SELECT id AS league_id, name AS league_name
FROM League;
"""
league_names = pd.read_sql_query(league_names_query, conn)

# Merge league names into the country_leagues_matches DataFrame
country_leagues_matches = country_leagues.merge(
    league_names, 
    on="league_id", 
    how="left"
)

country_leagues_matches.head()

match_api_id          home_team             away_team  home_team_goal  \
0        489042  Manchester United      Newcastle United               1   
1        489043            Arsenal  West Bromwich Albion               1   
2        489044         Sunderland             Liverpool               0   
3        489045    West Ham United        Wigan Athletic               2   
4        489046        Aston Villa       Manchester City               4   

   away_team_goal  homepos  awaypos  crosses  corners  yellow_cards  \
0               1       56       44        1        1             0   
1               0       65       35        1        1             0   
2               1       45       55        1        1             0   
3               1       50       50        1        1             0   
4               2       51       49        1        1             0   

   red_cards  fouls_committed     season  country_id  league_id  \
0          0                1  2008/2009        1729       1729   
1          0                1  2008/2009        1729       1729   
2          0                1  2008/2009        1729       1729   
3          0                1  2008/2009        1729       1729   
4          0                1  2008/2009        1729       1729   

              league_name  
0  England Premier League  
1  England Premier League  
2  England Premier League  
3  England Premier League  
4  England Premier League

1. Goal Distribution
Analysis:
This bar chart compares the total goals scored by home and away teams from ``2008-2009`` up until ``2015-2016``. It highlights whether home teams have an advantage in terms of scoring goals.

In [36]:
import plotly.graph_objects as go

# Visualization 1: Goal Distribution
fig1 = go.Figure()
fig1.add_trace(go.Bar(
    x=['Home Goals', 'Away Goals'],
    y=[country_leagues_matches['home_team_goal'].sum(), country_leagues_matches['away_team_goal'].sum()],
    marker_color=['blue', 'red']
))
fig1.update_layout(
    title="Goal Distribution: Home vs Away Teams",
    xaxis_title="Team Type",
    yaxis_title="Total Goals",
    template="plotly_white"
)
fig1.show()


2. Possession Comparison
Analysis:
This box plot compares ``possession`` percentages for ``home and away teams``. It helps identify trends in ball control and whether home teams consistently dominate possession.

In [37]:
# Visualization 2: Possession Comparison
fig2 = go.Figure()
fig2.add_trace(go.Box(y=country_leagues_matches['homepos'], name='Home Possession', boxmean=True))
fig2.add_trace(go.Box(y=country_leagues_matches['awaypos'], name='Away Possession', boxmean=True))
fig2.update_layout(
    title="Possession Comparison: Home vs Away Teams",
    yaxis_title="Possession (%)",
    template="plotly_white"
)
fig2.show()

3. Fouls and Cards Analysis
Analysis:
This stacked bar chart visualizes the relationship between ``fouls committed`` and ``cards`` received (yellow and red). It highlights teams with aggressive playstyles resulting in more cards.

In [38]:
# Visualization 3: Fouls and Cards Analysis
fig3 = go.Figure()
fig3.add_trace(go.Bar(
    x=country_leagues_matches['home_team'],
    y=country_leagues_matches['fouls_committed'],
    name='Fouls Committed',
    marker_color='orange'
))
fig3.add_trace(go.Bar(
    x=country_leagues_matches['home_team'],
    y=country_leagues_matches['yellow_cards'],
    name='Yellow Cards',
    marker_color='yellow'
))
fig3.add_trace(go.Bar(
    x=country_leagues_matches['home_team'],
    y=country_leagues_matches['red_cards'],
    name='Red Cards',
    marker_color='red'
))
fig3.update_layout(
    title="Fouls and Cards Analysis",
    xaxis_title="Teams",
    yaxis_title="Counts",
    barmode='stack',
    template="plotly_white"
)
fig3.show()


4. Seasonal Performance
Analysis:
This line chart tracks the average ``goals`` scored per season. It helps identify trends or shifts in scoring across different seasons.

In [39]:
# Visualization 4: Seasonal Performance
average_goals_per_season = country_leagues_matches.groupby('season').apply(
    lambda x: (x['home_team_goal'] + x['away_team_goal']).mean()
)
fig4 = go.Figure()
fig4.add_trace(go.Scatter(
    x=average_goals_per_season.index,
    y=average_goals_per_season.values,
    mode='lines+markers',
    line=dict(color='blue')
))
fig4.update_layout(
    title="Seasonal Performance: Average Goals per Season",
    xaxis_title="Season",
    yaxis_title="Average Goals",
    template="plotly_white"
)
fig4.show()


5. Crosses and Corners Comparison
Analysis:
This scatter plot shows the relationship between ``crosses`` and ``corners``. It identifies matches or teams with strong wing play leading to set pieces.

7. League-Level Comparison
Analysis:
This grouped bar chart compares average ``goals``, ``possession``, or ``fouls`` across leagues (league_id). It highlights differences in playing styles between leagues.

8. Home vs Away Advantage
Analysis:
This heatmap visualizes differences in performance metrics ``(e.g., goals, possession, fouls)`` between ``home and away teams``. It helps highlight home-field advantages.

In [ ]:
# Visualization 8: Home vs Away Advantage
fig8 = go.Figure(data=go.Heatmap(
    z=[
        country_leagues_matches['home_team_goal'] - country_leagues_matches['away_team_goal'],
        country_leagues_matches['homepos'] - country_leagues_matches['awaypos'],
        country_leagues_matches['fouls_committed']
    ],
    x=['Goal Difference', 'Possession Difference', 'Fouls Committed'],
    y=['Match'],
    colorscale='Viridis'
))
fig8.update_layout(
    title="Home vs Away Advantage",
    xaxis_title="Metric",
    yaxis_title="Match ID",
    template="plotly_white"
)
fig8.show()


9. Match Results by Season
Analysis:
This stacked bar chart shows the proportion of ``wins, losses, and draws`` for all matches in each ``season`` (season).

In [ ]:
# Visualization 9: Match Results by Season
season_results = country_leagues_matches.groupby('season').apply(
    lambda x: pd.Series({
        'Home Wins': (x['home_team_goal'] > x['away_team_goal']).sum(),
        'Away Wins': (x['home_team_goal'] < x['away_team_goal']).sum(),
        'Draws': (x['home_team_goal'] == x['away_team_goal']).sum()
    })
)
fig9 = go.Figure()
for result_type, color in zip(['Home Wins', 'Away Wins', 'Draws'], ['blue', 'red', 'gray']):
    fig9.add_trace(go.Bar(
        x=season_results.index,
        y=season_results[result_type],
        name=result_type,
        marker_color=color
    ))
fig9.update_layout(
    title="Match Results by Season",
    xaxis_title="Season",
    yaxis_title="Number of Matches",
    barmode='stack',
    template="plotly_white"
)
fig9.show()


10. High-Scoring Matches
Analysis:
This scatter plot highlights matches with high combined goals ``(home_team_goal + away_team_goal)``, helping identify thrilling matches.

In [ ]:
# Visualization 10: High-Scoring Matches
country_leagues_matches['total_goals'] = country_leagues_matches['home_team_goal'] + country_leagues_matches['away_team_goal']
fig10 = go.Figure()
fig10.add_trace(go.Scatter(
    x=country_leagues_matches['match_api_id'],
    y=country_leagues_matches['total_goals'],
    mode='markers',
    marker=dict(color='orange', size=10),
    text=country_leagues_matches['home_team'] + ' vs ' + country_leagues_matches['away_team']
))
fig10.update_layout(
    title="High-Scoring Matches",
    xaxis_title="Match ID",
    yaxis_title="Total Goals",
    template="plotly_white"
)
fig10.show()


11. Goals Per League
Analysis:
This bar chart shows the total ``goals`` scored in each ``league``, split between home and away teams.

In [ ]:
import plotly.graph_objects as go

# Count matches by league
league_match_counts = country_leagues_matches['league_name'].value_counts()

# Create the pie chart
fig = go.Figure(data=[go.Pie(
    labels=league_match_counts.index, 
    values=league_match_counts.values, 
    hole=0.3
)])

# Update the layout
fig.update_layout(
    title="Distribution of Matches by League Name",
    template="plotly_white"
)

# Display the chart
fig.show()


In [ ]:
import plotly.graph_objects as go

# Filter the dataset for a specific season
season_filtered = country_leagues_matches[country_leagues_matches['season'] == "2008/2009"]

# Count matches by league for the selected season
league_match_counts_season = season_filtered['league_name'].value_counts()

# Create the pie chart
fig = go.Figure(data=[go.Pie(
    labels=league_match_counts_season.index, 
    values=league_match_counts_season.values, 
    hole=0.3
)])

# Update the layout
fig.update_layout(
    title="Distribution of Matches by League Name (2008/2009 Season)",
    template="plotly_white"
)

# Display the chart
fig.show()


In [63]:
def calculate_league_ranking_simple(dataframe, league_name, season):
    """
    Calculate rankings for a specific league in a given season.

    Parameters:
        dataframe (pd.DataFrame): Matches dataset.
        league_name (str): League ID.
        season (str): Season (e.g., "2015/2016").

    Returns:
        pd.DataFrame: Rankings of teams.
    """
    # Filter for the given league and season
    data = dataframe[(dataframe['league_id'] == league_name) & (dataframe['season'] == season)]

    if data.empty:
        print(f"No data available for league ID {league_name} in {season}")
        return pd.DataFrame()

    # Calculate points
    data['home_points'] = (data['home_team_goal'] > data['away_team_goal']) * 3 + (data['home_team_goal'] == data['away_team_goal'])
    data['away_points'] = (data['away_team_goal'] > data['home_team_goal']) * 3 + (data['home_team_goal'] == data['away_team_goal'])

    # Aggregate stats
    home_stats = data.groupby('home_team').agg(
        points=('home_points', 'sum'),
        goals_scored=('home_team_goal', 'sum'),
        goals_conceded=('away_team_goal', 'sum')
    ).rename_axis('team').reset_index()

    away_stats = data.groupby('away_team').agg(
        points=('away_points', 'sum'),
        goals_scored=('away_team_goal', 'sum'),
        goals_conceded=('home_team_goal', 'sum')
    ).rename_axis('team').reset_index()

    # Combine home and away stats
    rankings = pd.concat([home_stats, away_stats]).groupby('team').sum().reset_index()

    # Calculate goal difference
    rankings['goal_difference'] = rankings['goals_scored'] - rankings['goals_conceded']

    # Sort by points, goal difference, and goals scored
    rankings = rankings.sort_values(['points', 'goal_difference', 'goals_scored'], ascending=[False, False, False])

    # Add a rank column
    rankings.reset_index(drop=True, inplace=True)
    rankings.index += 1
    rankings.rename_axis("Rank", inplace=True)

    return rankings

# Example usage
league_ranking = calculate_league_ranking_simple(country_leagues_matches, 1729, "2015/2016")
league_ranking.head(20)

/tmp/ipykernel_316084/2887692606.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_316084/2887692606.py:22: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



team  points  goals_scored  goals_conceded  \
Rank                                                               
1           Leicester City      81            68              36   
2                  Arsenal      71            65              36   
3        Tottenham Hotspur      70            69              35   
4          Manchester City      66            71              41   
5        Manchester United      66            49              35   
6              Southampton      63            59              41   
7          West Ham United      62            65              51   
8                Liverpool      60            63              50   
9               Stoke City      51            41              55   
10                 Chelsea      50            59              53   
11                 Everton      47            59              55   
12            Swansea City      47            42              52   
13                 Watford      45            40              50   
14    West Bromwich Albion      43            34              48   
15          Crystal Palace      42            39              51   
16             Bournemouth      42            45              67   
17              Sunderland      39            48              62   
18        Newcastle United      37            44              65   
19            Norwich City      34            39              67   
20             Aston Villa      17            27              76   

      goal_difference  
Rank                   
1                  32  
2                  29  
3                  34  
4                  30  
5                  14  
6                  18  
7                  14  
8                  13  
9                 -14  
10                  6  
11                  4  
12                -10  
13                -10  
14                -14  
15                -12  
16                -22  
17                -14  
18                -21  
19                -28  
20                -49

In [69]:
# Goals Scored vs Goals Conceded
if not league_ranking.empty:
    fig = go.Figure()

    # Add a scatter plot
    fig.add_trace(go.Scatter(
        x=league_ranking['goals_conceded'],
        y=league_ranking['goals_scored'],
        mode='markers+text',
        text=league_ranking['team'],
        marker=dict(size=10, color='#ff3300'),
        name="Goals Scored vs Conceded"
    ))

    # Update layout
    fig.update_layout(
        title="Goals Scored vs Goals Conceded: England Premier League 2015/2016",
        xaxis_title="Goals Conceded",
        yaxis_title="Goals Scored",
        template="plotly_white"
    )

    # Show the visualization
    fig.show()
else:
    print("No data available for visualization.")

In [68]:
# Points Distribution Across Teams
if not league_ranking.empty:
    fig = go.Figure()

    # Add a horizontal bar chart for points
    fig.add_trace(go.Bar(
        y=league_ranking['team'],
        x=league_ranking['points'],
        name='Points',
        orientation='h',
        marker_color='#00bbff'
    ))

    # Update layout
    fig.update_layout(
        title="Points Distribution: England Premier League 2015/2016",
        xaxis_title="Points",
        yaxis_title="Team",
        template="plotly_white"
    )

    # Show the visualization
    fig.show()
else:
    print("No data available for visualization.")

In [71]:
# Total Goals by Team in a League
if not league_ranking.empty:
    fig = go.Figure()

    # Add a bar chart for total goals scored
    fig.add_trace(go.Bar(
        x=league_ranking['team'],  # Correct column name
        y=league_ranking['goals_scored'],
        name='Goals Scored',
        marker_color='springgreen'
    ))

    # Update layout
    fig.update_layout(
        title="Total Goals by Team: England Premier League 2008/2009",
        xaxis_title="Team",
        yaxis_title="Goals Scored",
        template="plotly_white"
    )

    # Show the visualization
    fig.show()
else:
    print("No data available for visualization.")

In [73]:
# Calculate total goals per league
total_goals_per_league = country_leagues_matches.groupby('league_name').agg(
    home_goals=('home_team_goal', 'sum'),
    away_goals=('away_team_goal', 'sum')
).reset_index()

# Add total goals column
total_goals_per_league['total_goals'] = total_goals_per_league['home_goals'] + total_goals_per_league['away_goals']

# Sort by total goals to identify the highest-scoring leagues
total_goals_per_league = total_goals_per_league.sort_values('total_goals', ascending=False)

total_goals_per_league.head()


league_name  home_goals  away_goals  total_goals
7         Spain LIGA BBVA        4958        3451         8409
0  England Premier League        4715        3525         8240
3           Italy Serie A        4527        3362         7889
2   Germany 1. Bundesliga        3982        3121         7103
1          France Ligue 1        2905        2122         5027

In [75]:
# Visualization: Bar chart for the highest-scoring leagues
fig = go.Figure()

fig.add_trace(go.Bar(
    x=total_goals_per_league['league_name'].astype(str),
    y=total_goals_per_league['total_goals'],
    marker_color='#ff008c'
))

fig.update_layout(
    title="Highest Scoring Leagues",
    xaxis_title="League ID",
    yaxis_title="Total Goals Scored",
    template="plotly_white"
)

# Show the visualization
fig.show()

In [83]:
# Calculate total goals scored by each team per league
top_scorers_per_league = country_leagues_matches.groupby(['league_name', 'home_team']).agg(
    home_goals=('home_team_goal', 'sum')
).reset_index()

away_goals_per_league = country_leagues_matches.groupby(['league_name', 'away_team']).agg(
    away_goals=('away_team_goal', 'sum')
).reset_index()

# Combine home and away goals
top_scorers = pd.merge(
    top_scorers_per_league, 
    away_goals_per_league, 
    left_on=['league_name', 'home_team'], 
    right_on=['league_name', 'away_team'], 
    how='outer'
).fillna(0)

# Calculate total goals for each team
top_scorers['team'] = top_scorers['home_team'].combine_first(top_scorers['away_team'])
top_scorers['total_goals'] = top_scorers['home_goals'] + top_scorers['away_goals']

# Get the top scorer for each league
top_scorers_per_league = top_scorers.groupby('league_name').apply(
    lambda x: x.nlargest(1, 'total_goals')
).reset_index(drop=True)

top_scorers_per_league.head()

league_name            home_team  home_goals  \
0  England Premier League      Manchester City       365.0   
1          France Ligue 1  Paris Saint-Germain       248.0   
2   Germany 1. Bundesliga     FC Bayern Munich       382.0   
3           Italy Serie A             Juventus       307.0   
4  Netherlands Eredivisie                  PSV        77.0   

             away_team  away_goals                 team  total_goals  
0      Manchester City       241.0      Manchester City        606.0  
1  Paris Saint-Germain       177.0  Paris Saint-Germain        425.0  
2     FC Bayern Munich       271.0     FC Bayern Munich        653.0  
3             Juventus       236.0             Juventus        543.0  
4                  PSV        81.0                  PSV        158.0

In [84]:
# Visualization: Top Scorers Per League
fig = go.Figure()

fig.add_trace(go.Bar(
    x=top_scorers_per_league['league_name'].astype(str),
    y=top_scorers_per_league['total_goals'],
    text=top_scorers_per_league['team'],
    marker_color='#aa00ff'
))
fig.update_layout(
    title="Top Scorers Per League",
    xaxis_title="League Name",
    yaxis_title="Total Goals Scored",
    template="plotly_white"
)

# Show the visualization
fig.show()

In [87]:
# Calculate average goals per league
avg_goals_per_league = country_leagues_matches.groupby('league_name').agg(
    avg_home_goals=('home_team_goal', 'mean'),
    avg_away_goals=('away_team_goal', 'mean')
).reset_index()

avg_goals_per_league['avg_total_goals'] = avg_goals_per_league['avg_home_goals'] + avg_goals_per_league['avg_away_goals']
avg_goals_per_league.head()

league_name  avg_home_goals  avg_away_goals  avg_total_goals
0  England Premier League        1.550987        1.159539         2.710526
1          France Ligue 1        1.433860        1.047384         2.481244
2   Germany 1. Bundesliga        1.626634        1.274918         2.901552
3           Italy Serie A        1.501991        1.115461         2.617452
4  Netherlands Eredivisie        1.649057        1.356604         3.005660

In [88]:
# Visualization: Average Goals per League
fig = go.Figure()

fig.add_trace(go.Bar(
    x=avg_goals_per_league['league_name'].astype(str),
    y=avg_goals_per_league['avg_total_goals'],
    marker_color='grey',
    name="Average Total Goals"
))

fig.update_layout(
    title="Average Goals Scored Per Match by League",
    xaxis_title="League Name",
    yaxis_title="Average Goals Per Match",
    template="plotly_white"
)

fig.show()

In [94]:
# Calculate points for each league
league_competitiveness = country_leagues_matches.groupby(['league_name', 'home_team']).agg(
    home_points=('home_team_goal', 'sum'),
    away_points=('away_team_goal', 'sum')
).reset_index()

league_competitiveness['total_points'] = league_competitiveness['home_points'] + league_competitiveness['away_points']

# Calculate range of points (difference between top and bottom)
league_point_range = league_competitiveness.groupby('league_name')['total_points'].agg(
    max_points='max',
    min_points='min'
).reset_index()

league_point_range['point_range'] = league_point_range['max_points'] - league_point_range['min_points']
league_competitiveness.head()

league_name         home_team  home_points  away_points  \
0  England Premier League           Arsenal          306          122   
1  England Premier League       Aston Villa          179          198   
2  England Premier League   Birmingham City           38           35   
3  England Premier League  Blackburn Rovers           98           90   
4  England Premier League         Blackpool           30           37   

   total_points  
0           428  
1           377  
2            73  
3           188  
4            67

In [95]:
# Visualization: Competitiveness of Leagues
fig = go.Figure()

fig.add_trace(go.Bar(
    x=league_point_range['league_name'].astype(str),
    y=league_point_range['point_range'],
    marker_color='red',
    name="Point Range"
))

fig.update_layout(
    title="Point Range (Competitiveness) by League",
    xaxis_title="League Name",
    yaxis_title="Point Range",
    template="plotly_white"
)

fig.show()

In [102]:
# Calculate total goals per season for each league
scoring_trends = country_leagues_matches.groupby(['league_name', 'season']).agg(
    home_goals=('home_team_goal', 'sum'),
    away_goals=('away_team_goal', 'sum')
).reset_index()

# Add total goals column
scoring_trends['total_goals'] = scoring_trends['home_goals'] + scoring_trends['away_goals']
scoring_trends.head()

league_name     season  home_goals  away_goals  total_goals
0  England Premier League  2008/2009         532         410          942
1  England Premier League  2009/2010         645         408         1053
2  England Premier League  2010/2011         617         446         1063
3  England Premier League  2011/2012         604         462         1066
4  England Premier League  2012/2013         592         471         1063

In [104]:
# Visualization: Scoring Trends Over Seasons
fig = go.Figure()

for league in scoring_trends['league_name'].unique():
    league_data = scoring_trends[scoring_trends['league_name'] == league]
    fig.add_trace(go.Scatter(
        x=league_data['season'],
        y=league_data['total_goals'],
        mode='lines+markers',
        name=f"League {league}"
    ))

fig.update_layout(
    title="Scoring Trends Over Seasons by League",
    xaxis_title="Season",
    yaxis_title="Total Goals",
    template="plotly_white"
)

fig.show()

In [106]:
# Calculate average fouls per league
avg_fouls_per_league = country_leagues_matches.groupby('league_name').agg(
    avg_fouls=('fouls_committed', 'mean')
).reset_index()
avg_fouls_per_league.head()


league_name  avg_fouls
0  England Premier League   1.000000
1          France Ligue 1   0.377098
2   Germany 1. Bundesliga   0.463644
3           Italy Serie A   0.513935
4  Netherlands Eredivisie   0.609434

In [107]:
# Visualization: Fouls Per Match by League
fig = go.Figure()

fig.add_trace(go.Bar(
    x=avg_fouls_per_league['league_name'].astype(str),
    y=avg_fouls_per_league['avg_fouls'],
    marker_color='orange',
    name="Average Fouls"
))

fig.update_layout(
    title="Average Fouls Committed Per Match by League",
    xaxis_title="League Name",
    yaxis_title="Average Fouls",
    template="plotly_white"
)

fig.show()

In [108]:
team_data.head()

id  team_api_id  team_fifa_api_id     team_long_name team_short_name
0   1         9987             673.0           KRC Genk             GEN
1   2         9993             675.0       Beerschot AC             BAC
2   3        10000           15005.0   SV Zulte-Waregem             ZUL
3   4         9994            2007.0   Sporting Lokeren             LOK
4   5         9984            1750.0  KSV Cercle Brugge             CEB

In [109]:
team_attributes_data.head()

id  team_fifa_api_id  team_api_id                 date  buildUpPlaySpeed  \
0   1               434         9930  2010-02-22 00:00:00                60   
1   2               434         9930  2014-09-19 00:00:00                52   
2   3               434         9930  2015-09-10 00:00:00                47   
3   4                77         8485  2010-02-22 00:00:00                70   
4   5                77         8485  2011-02-22 00:00:00                47   

  buildUpPlaySpeedClass  buildUpPlayDribbling buildUpPlayDribblingClass  \
0              Balanced                   NaN                    Little   
1              Balanced                  48.0                    Normal   
2              Balanced                  41.0                    Normal   
3                  Fast                   NaN                    Little   
4              Balanced                   NaN                    Little   

   buildUpPlayPassing buildUpPlayPassingClass  ... chanceCreationShooting  \
0                  50                   Mixed  ...                     55   
1                  56                   Mixed  ...                     64   
2                  54                   Mixed  ...                     64   
3                  70                    Long  ...                     70   
4                  52                   Mixed  ...                     52   

   chanceCreationShootingClass chanceCreationPositioningClass  \
0                       Normal                      Organised   
1                       Normal                      Organised   
2                       Normal                      Organised   
3                         Lots                      Organised   
4                       Normal                      Organised   

   defencePressure defencePressureClass  defenceAggression  \
0               50               Medium                 55   
1               47               Medium                 44   
2               47               Medium                 44   
3               60               Medium                 70   
4               47               Medium                 47   

  defenceAggressionClass defenceTeamWidth  defenceTeamWidthClass  \
0                  Press               45                 Normal   
1                  Press               54                 Normal   
2                  Press               54                 Normal   
3                 Double               70                   Wide   
4                  Press               52                 Normal   

  defenceDefenderLineClass  
0                    Cover  
1                    Cover  
2                    Cover  
3                    Cover  
4                    Cover  

[5 rows x 25 columns]

In [111]:
Teams = team_attributes_data.merge(team_data[['team_api_id', 'team_long_name', 'team_short_name']], how='left', on='team_api_id').reset_index()

In [112]:
Teams.head()

index  id  team_fifa_api_id  team_api_id                 date  \
0      0   1               434         9930  2010-02-22 00:00:00   
1      1   2               434         9930  2014-09-19 00:00:00   
2      2   3               434         9930  2015-09-10 00:00:00   
3      3   4                77         8485  2010-02-22 00:00:00   
4      4   5                77         8485  2011-02-22 00:00:00   

   buildUpPlaySpeed buildUpPlaySpeedClass  buildUpPlayDribbling  \
0                60              Balanced                   NaN   
1                52              Balanced                  48.0   
2                47              Balanced                  41.0   
3                70                  Fast                   NaN   
4                47              Balanced                   NaN   

  buildUpPlayDribblingClass  buildUpPlayPassing  ...  \
0                    Little                  50  ...   
1                    Normal                  56  ...   
2                    Normal                  54  ...   
3                    Little                  70  ...   
4                    Little                  52  ...   

  chanceCreationPositioningClass defencePressure  defencePressureClass  \
0                      Organised              50                Medium   
1                      Organised              47                Medium   
2                      Organised              47                Medium   
3                      Organised              60                Medium   
4                      Organised              47                Medium   

  defenceAggression  defenceAggressionClass defenceTeamWidth  \
0                55                   Press               45   
1                44                   Press               54   
2                44                   Press               54   
3                70                  Double               70   
4                47                   Press               52   

   defenceTeamWidthClass defenceDefenderLineClass team_long_name  \
0                 Normal                    Cover       FC Aarau   
1                 Normal                    Cover       FC Aarau   
2                 Normal                    Cover       FC Aarau   
3                   Wide                    Cover       Aberdeen   
4                 Normal                    Cover       Aberdeen   

   team_short_name  
0              AAR  
1              AAR  
2              AAR  
3              ABE  
4              ABE  

[5 rows x 28 columns]

In [122]:
# Handle missing values:
# Fill missing values with appropriate methods, e.g., fill NaN in numeric columns with the mean or median, 
# and in categorical columns with the mode (most frequent value).
Teams['buildUpPlayDribbling'].fillna(Teams['buildUpPlayDribbling'].mode()[0], inplace=True)

# Check and remove duplicates if any
Teams.drop_duplicates(inplace=True)

# Convert relevant columns to the appropriate data types
Teams['date'] = pd.to_datetime(Teams['date'])  # Convert date column to datetime type
numeric_cols = ['buildUpPlaySpeed', 'buildUpPlayPassing', 'defencePressure', 'defenceAggression', 'defenceTeamWidth']  # Example of numeric columns
Teams[numeric_cols] = Teams[numeric_cols].apply(pd.to_numeric, errors='coerce')  # Ensure numeric columns are treated as numbers

In [123]:
Teams.head()

index  id  team_fifa_api_id  team_api_id       date  buildUpPlaySpeed  \
0      0   1               434         9930 2010-02-22                60   
1      1   2               434         9930 2014-09-19                52   
2      2   3               434         9930 2015-09-10                47   
3      3   4                77         8485 2010-02-22                70   
4      4   5                77         8485 2011-02-22                47   

  buildUpPlaySpeedClass  buildUpPlayDribbling buildUpPlayDribblingClass  \
0              Balanced                  52.0                    Little   
1              Balanced                  48.0                    Normal   
2              Balanced                  41.0                    Normal   
3                  Fast                  52.0                    Little   
4              Balanced                  52.0                    Little   

   buildUpPlayPassing  ... chanceCreationPositioningClass defencePressure  \
0                  50  ...                      Organised              50   
1                  56  ...                      Organised              47   
2                  54  ...                      Organised              47   
3                  70  ...                      Organised              60   
4                  52  ...                      Organised              47   

   defencePressureClass defenceAggression  defenceAggressionClass  \
0                Medium                55                   Press   
1                Medium                44                   Press   
2                Medium                44                   Press   
3                Medium                70                  Double   
4                Medium                47                   Press   

  defenceTeamWidth  defenceTeamWidthClass defenceDefenderLineClass  \
0               45                 Normal                    Cover   
1               54                 Normal                    Cover   
2               54                 Normal                    Cover   
3               70                   Wide                    Cover   
4               52                 Normal                    Cover   

  team_long_name  team_short_name  
0       FC Aarau              AAR  
1       FC Aarau              AAR  
2       FC Aarau              AAR  
3       Aberdeen              ABE  
4       Aberdeen              ABE  

[5 rows x 28 columns]

In [125]:
# Get summary statistics for numeric columns
print(Teams.describe())

# Check for missing values
print(Teams.isnull().sum())

             index           id  team_fifa_api_id    team_api_id  \
count  1458.000000  1458.000000       1458.000000    1458.000000   
mean    728.500000   729.500000      17706.982167    9995.727023   
min       0.000000     1.000000          1.000000    1601.000000   
25%     364.250000   365.250000        110.000000    8457.750000   
50%     728.500000   729.500000        485.000000    8674.000000   
75%    1092.750000  1093.750000       1900.000000    9904.000000   
max    1457.000000  1458.000000     112513.000000  274581.000000   
std     421.032659   421.032659      39179.857739   13264.869900   

                                date  buildUpPlaySpeed  buildUpPlayDribbling  \
count                           1458       1458.000000           1458.000000   
mean   2012-12-06 22:40:59.259259392         52.462277             50.862140   
min              2010-02-22 00:00:00         20.000000             24.000000   
25%              2011-02-22 00:00:00         45.000000             

In [126]:
# Create a bar plot for 'buildUpPlaySpeedClass'
fig = go.Figure()

fig.add_trace(go.Bar(
    x=Teams['buildUpPlaySpeedClass'].value_counts().index,
    y=Teams['buildUpPlaySpeedClass'].value_counts().values,
    marker=dict(color='royalblue')
))

# Update the layout for the bar plot
fig.update_layout(
    title='Distribution of BuildUpPlaySpeedClass',
    xaxis_title='BuildUpPlaySpeedClass',
    yaxis_title='Count'
)

# Show the figure
fig.show()